# Create Orpheus Onnx model from Huggingface model

## First install all the prerequisits

In [13]:
!sudo apt-get update -q && sudo apt-get dist-upgrade -y -q

Hit:1 https://cloud.r-project.org/bin/linux/ubuntu jammy-cran40/ InRelease
Hit:2 https://developer.download.nvidia.com/compute/cuda/repos/ubuntu2204/x86_64  InRelease
Hit:3 http://archive.ubuntu.com/ubuntu jammy InRelease
Get:4 http://security.ubuntu.com/ubuntu jammy-security InRelease [129 kB]
Hit:5 http://archive.ubuntu.com/ubuntu jammy-updates InRelease
Hit:6 http://archive.ubuntu.com/ubuntu jammy-backports InRelease
Hit:7 https://r2u.stat.illinois.edu/ubuntu jammy InRelease
Hit:8 https://ppa.launchpadcontent.net/deadsnakes/ppa/ubuntu jammy InRelease
Hit:9 https://ppa.launchpadcontent.net/graphics-drivers/ppa/ubuntu jammy InRelease
Hit:10 https://ppa.launchpadcontent.net/ubuntugis/ppa/ubuntu jammy InRelease
Fetched 129 kB in 2s (77.8 kB/s)
Reading package lists...
W: Skipping acquire of configured file 'main/source/Sources' as repository 'https://r2u.stat.illinois.edu/ubuntu jammy InRelease' does not seem to provide it (sources.list entry misspelt?)
Reading package lists...
Building

In [15]:
%pip install torch torchvision torchaudio

In [16]:
%pip install --pre onnx onnxruntime onnxruntime-genai

In [32]:
%pip install transformers accelerate peft bitsandbytes snac gguf hf_xet huggingface_hub[hf_xet]


In [14]:
!nvidia-smi

Fri May 16 18:29:15 2025       
+-----------------------------------------------------------------------------------------+
| NVIDIA-SMI 550.54.15              Driver Version: 550.54.15      CUDA Version: 12.4     |
|-----------------------------------------+------------------------+----------------------+
| GPU  Name                 Persistence-M | Bus-Id          Disp.A | Volatile Uncorr. ECC |
| Fan  Temp   Perf          Pwr:Usage/Cap |           Memory-Usage | GPU-Util  Compute M. |
|                                         |                        |               MIG M. |
|=========================================+========================+======================|
|   0  Tesla T4                       Off |   00000000:00:04.0 Off |                    0 |
| N/A   45C    P8              9W /   70W |       0MiB /  15360MiB |      0%      Default |
|                                         |                        |                  N/A |
+-----------------------------------------+-----

## Clone the the OnnxRuntime for GenAI repo

In [3]:
!git clone https://github.com/microsoft/onnxruntime-genai --depth=1

Cloning into 'onnxruntime-genai'...
Updating files:   5% (35/649)
Updating files:   6% (39/649)
Updating files:   7% (46/649)
Updating files:   8% (52/649)
Updating files:   9% (59/649)
Updating files:  10% (65/649)
Updating files:  11% (72/649)
Updating files:  12% (78/649)
Updating files:  13% (85/649)
Updating files:  14% (91/649)
Updating files:  15% (98/649)
Updating files:  16% (104/649)
Updating files:  17% (111/649)
Updating files:  18% (117/649)
Updating files:  19% (124/649)
Updating files:  20% (130/649)
Updating files:  21% (137/649)
Updating files:  22% (143/649)
Updating files:  23% (150/649)
Updating files:  24% (156/649)
Updating files:  25% (163/649)
Updating files:  26% (169/649)
Updating files:  27% (176/649)
Updating files:  28% (182/649)
Updating files:  29% (189/649)
Updating files:  30% (195/649)
Updating files:  31% (202/649)
Updating files:  32% (208/649)
Updating files:  33% (215/649)
Updating files:  34% (221/649)
Updating files:  35% (228/649)
Updating files

In [ ]:
!huggingface-cli login

In [27]:
!python3 -m onnxruntime-genai.build --help

usage: build.py [-h] [--build_dir BUILD_DIR]
                [--config {Debug,MinSizeRel,Release,RelWithDebInfo}]
                [--update] [--build] [--test] [--package] [--clean]
                [--skip_tests] [--skip_wheel] [--build_csharp] [--build_java]
                [--parallel] [--cmake_path CMAKE_PATH]
                [--ctest_path CTEST_PATH]
                [--cmake_generator {MinGW Makefiles,Ninja,NMake Makefiles,Unix Makefiles,Visual Studio 17 2022,Xcode}]
                [--cmake_extra_defines CMAKE_EXTRA_DEFINES [CMAKE_EXTRA_DEFINES ...]]
                [--ort_home ORT_HOME] [--use_cuda] [--cuda_home CUDA_HOME]
                [--use_rocm] [--use_dml] [--use_guidance]
                [--android | --ios | --macos {MacOSX,Catalyst}]
                [--android_abi {armeabi-v7a,arm64-v8a,x86,x86_64}]
                [--android_api ANDROID_API] [--android_home ANDROID_HOME]
                [--android_ndk_path ANDROID_NDK_PATH] [--android_run_emulator]
                [--ap

In [ ]:
!huggingface-cli download Prince-1/orpheus_3b_0.1_GGUF --include unsloth.Q4_0.gguf  --local-dir gguf

'GGUF/unsloth.F16.gguf'

In [1]:
!huggingface-cli download Prince-1/orpheus_3b_0.1_ft_16bit  --local-dir main

^C


## Build Onnx Model from HUggingface model

In [50]:
!python {script_path} -m "Prince-1/orpheus_3b_0.1_ft_16bit" -i "/content/GGUF/unsloth.F16.gguf" -o "/content/onnx" -p "fp16"  -e cuda

2025-05-16 19:21:08,458 numexpr.utils [INFO] - NumExpr defaulting to 2 threads.
Valid precision + execution provider combinations are: FP32 CPU, FP32 CUDA, FP16 CUDA, FP16 DML, BF16 CUDA, INT4 CPU, INT4 CUDA, INT4 DML, INT4 WEBGPU
Extra options: {}
GroupQueryAttention (GQA) is used in this model.
Reading embedding layer
Reading decoder layer 0
Reading decoder layer 1
Reading decoder layer 2
Reading decoder layer 3
Reading decoder layer 4
Reading decoder layer 5
Reading decoder layer 6
Reading decoder layer 7
Reading decoder layer 8
Reading decoder layer 9
Reading decoder layer 10
Reading decoder layer 11
Reading decoder layer 12
Reading decoder layer 13
Reading decoder layer 14
Reading decoder layer 15
Reading decoder layer 16
^C


## Build the Onnx Model from GGUF Model

In [ ]:
script_path = "onnxruntime-genai/src/python/py/models/builder.py"
!python {script_path} -m "Prince-1/orpheus_3b_0.1_ft_16bit" -i "main" -o "onnx" -p "fp16"  -e cuda

2025-05-16 19:09:09,888 numexpr.utils [INFO] - NumExpr defaulting to 2 threads.
Valid precision + execution provider combinations are: FP32 CPU, FP32 CUDA, FP16 CUDA, FP16 DML, BF16 CUDA, INT4 CPU, INT4 CUDA, INT4 DML, INT4 WEBGPU
Extra options: {}
GroupQueryAttention (GQA) is used in this model.
Reading embedding layer
Reading decoder layer 0
Reading decoder layer 1
Reading decoder layer 2
Reading decoder layer 3
Reading decoder layer 4
Reading decoder layer 5
Reading decoder layer 6
Reading decoder layer 7
Reading decoder layer 8
Reading decoder layer 9
Reading decoder layer 10
Reading decoder layer 11
Reading decoder layer 12
Reading decoder layer 13
Reading decoder layer 14
Reading decoder layer 15
Reading decoder layer 16
^C
